# Flux Density (𝐃)

$$ \dot{𝐃} = ∇ × 𝐇     \tag{2.1a} $$

$$ 𝐃(ω) = ε_0 ⋅ ε_r^*(ω) ⋅ 𝐄(ω)     \tag{2.1b} $$
$$ μ_0 ⋅ \dot{𝐇} = - ∇ × 𝐄          \tag{2.1c} $$

$$ \tilde{𝐄} = \sqrt{ε_0/μ_0} ⋅ 𝐄           \tag{2.2a} $$
$$ \tilde{𝐃} = \sqrt{1/(ε_0 μ_0)} ⋅ 𝐃       \tag{2.2b} $$

$$ \dot{\tilde{𝐃}} = (1/\sqrt{ε_0 μ_0}) ∇ × 𝐇       \tag{2.3a} $$

$$ \tilde{𝐃}(ω) = ε_r^*(ω) ⋅ \tilde{𝐄}(ω)            \tag{2.3b} $$

$$ \dot{𝐇} = - 1/\sqrt{ε_0 μ_0} ∇ × \tilde{𝐄}       \tag{2.3c} $$

$$  ε_r^*(ω) = ε_r + \frac{σ}{jω ⋅ ε_0}         \tag{2.4}  $$

$$ \tilde{𝐃} → 𝐃 , \tilde{𝐄} → 𝐄  $$

$$ 𝐃(ω) = ε_r 𝐄(ω) + \frac{σ}{jω ⋅ ε_0} 𝐄(ω)       \tag{2.5}  $$


$$ ω → t $$

$$ 𝐃(t) = ε_r 𝐄(t) + \frac{σ}{ε_0}∫_0^t 𝐄(t') dt'  $$

$$ 𝐃^n = ε_r 𝐄^n + \frac{σ ⋅ Δt}{ε_0}∑_{i=0}^n 𝐄^i          \tag{2.6} $$

$$ 𝐃^n = ε_r 𝐄^n + \frac{σ ⋅ Δt}{ε_0} 𝐄^n  + \frac{σ ⋅ Δt}{ε_0} ∑_{i=0}^{n-1} 𝐄^i $$

$$ 𝐄^n = \frac 
{𝐃^n - \frac{σ ⋅ Δt}{ε_0} ∑_{i=0}^{n-1} 𝐄^i}
{ε_r + \frac{σ ⋅ Δt}{ε_0}}
\tag{2.7} $$

$$  𝐈^{n-1} = \frac{σ ⋅ Δt}{ε_0} ∑_{i=0}^{n-1} 𝐄^i $$

$$ 𝐄^n = \frac{𝐃^n - 𝐈^{n-1}}{ε_r + \frac{σ ⋅ Δt}{ε_0}}
\tag{2.8a} $$

$$ 𝐈^n = 𝐈^{n-1} + \frac{σ ⋅ Δt}{ε_0} 𝐄^n       \tag{2.8b}  $$


In [1]:
import numpy  as np
from bokeh.plotting import output_notebook, figure, show, gridplot

output_notebook()

Loading BokehJS ...

In [2]:
ke = 200
nsteps = 500

Ex, Dx, Ix, Hy = [np.zeros([nsteps, ke]) for _ in range(4)]

ddx = 0.01  # cell size
dt = ddx / 6e8  # time step
freq_in = 700e6

bc_low = [0, 0]
bc_high = [0, 0]

# ε
epsz = 8.854e-12
epsr = 4
sigma = 0.04
k_start = 100

gax = np.ones(ke)
gbx = np.zeros(ke)
gax[k_start:] = 1 / (epsr + (sigma * dt / epsz))
gbx[k_start:] = sigma * dt / epsz

# FDTD
for ts in range(1, nsteps):
    # Dx
    for k in range(1, ke):
        ts_n = ts - 1
        Dx[ts, k] = Dx[ts_n, k] + 0.5 * (Hy[ts_n, k - 1] - Hy[ts_n, k])

    # sin pulse
    pulse = np.sin(2 * np.pi * freq_in * dt * ts)
    Dx[ts, 5] = pulse + Dx[ts, 5]

    # Ex from Dx[ts, :] - current time
    for k in range(1, ke):
        ts_n = ts - 1
        Ex[ts, k] = gax[k] * (Dx[ts, k] - Ix[ts_n, k])
        Ix[ts, k] = Ix[ts_n, k] + gbx[k] * Ex[ts, k] # Ex[ts, :] current time

    Ex[ts, 0] = bc_low.pop(0)
    bc_low.append(Ex[ts, 1])
    Ex[ts, ke - 1] = bc_high.pop(0)
    bc_high.append(Ex[ts, ke - 2])

    # Hy
    for k in range(ke - 1):
        ts_n = ts - 1
        Hy[ts, k] = Hy[ts_n, k] + 0.5 * (Ex[ts, k] - Ex[ts, k + 1])
    

In [3]:
_fparams = dict(width=900, height=300, x_axis_label="Z", y_axis_label="t")
fig_titles = "Ex Dx Ix Hy".split()
figs = [[figure(**_fparams, title=title)] for title in fig_titles]

_params = dict(level="image", x=0, y=0, dw=ke, dh=nsteps, palette="Turbo256")

for fig, hist in zip(figs, [Ex,Dx, Ix, Hy]):
    fig[0].image(image=[hist], **_params)

show(gridplot(figs))